In [1]:
import re

In [2]:
import numpy as np
import pandas as pd

In [3]:
from pprint import pprint

In [4]:
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

In [5]:
from nltk.corpus import stopwords

In [9]:
import spacy

In [10]:
stop_words = stopwords.words('english')
stop_words.extend(['from', 'subject', 're', 'edu', 'use'])

In [36]:
stop_words

['i',
 'me',
 'my',
 'myself',
 'we',
 'our',
 'ours',
 'ourselves',
 'you',
 "you're",
 "you've",
 "you'll",
 "you'd",
 'your',
 'yours',
 'yourself',
 'yourselves',
 'he',
 'him',
 'his',
 'himself',
 'she',
 "she's",
 'her',
 'hers',
 'herself',
 'it',
 "it's",
 'its',
 'itself',
 'they',
 'them',
 'their',
 'theirs',
 'themselves',
 'what',
 'which',
 'who',
 'whom',
 'this',
 'that',
 "that'll",
 'these',
 'those',
 'am',
 'is',
 'are',
 'was',
 'were',
 'be',
 'been',
 'being',
 'have',
 'has',
 'had',
 'having',
 'do',
 'does',
 'did',
 'doing',
 'a',
 'an',
 'the',
 'and',
 'but',
 'if',
 'or',
 'because',
 'as',
 'until',
 'while',
 'of',
 'at',
 'by',
 'for',
 'with',
 'about',
 'against',
 'between',
 'into',
 'through',
 'during',
 'before',
 'after',
 'above',
 'below',
 'to',
 'from',
 'up',
 'down',
 'in',
 'out',
 'on',
 'off',
 'over',
 'under',
 'again',
 'further',
 'then',
 'once',
 'here',
 'there',
 'when',
 'where',
 'why',
 'how',
 'all',
 'any',
 'both',
 'each

In [11]:
df = pd.read_json('newsgroups.json')
print(df.target_names.unique())
df

['rec.autos' 'comp.sys.mac.hardware' 'comp.graphics' 'sci.space'
 'talk.politics.guns' 'sci.med' 'comp.sys.ibm.pc.hardware'
 'comp.os.ms-windows.misc' 'rec.motorcycles' 'talk.religion.misc'
 'misc.forsale' 'alt.atheism' 'sci.electronics' 'comp.windows.x'
 'rec.sport.hockey' 'rec.sport.baseball' 'soc.religion.christian'
 'talk.politics.mideast' 'talk.politics.misc' 'sci.crypt']


content  target  \
0      From: lerxst@wam.umd.edu (where's my thing)\nS...       7   
1      From: guykuo@carson.u.washington.edu (Guy Kuo)...       4   
2      From: twillis@ec.ecn.purdue.edu (Thomas E Will...       4   
3      From: jgreen@amber (Joe Green)\nSubject: Re: W...       1   
4      From: jcm@head-cfa.harvard.edu (Jonathan McDow...      14   
...                                                  ...     ...   
11309  From: jim.zisfein@factory.com (Jim Zisfein) \n...      13   
11310  From: ebodin@pearl.tufts.edu\nSubject: Screen ...       4   
11311  From: westes@netcom.com (Will Estes)\nSubject:...       3   
11312  From: steve@hcrlgw (Steven Collins)\nSubject: ...       1   
11313  From: gunning@cco.caltech.edu (Kevin J. Gunnin...       8   

                   target_names  
0                     rec.autos  
1         comp.sys.mac.hardware  
2         comp.sys.mac.hardware  
3                 comp.graphics  
4                     sci.space  
...                         ...  
11309                   sci.med  
11310     comp.sys.mac.hardware  
11311  comp.sys.ibm.pc.hardware  
11312             comp.graphics  
11313           rec.motorcycles  

[11314 rows x 3 columns]

In [12]:
df.loc[1,'content']

"From: guykuo@carson.u.washington.edu (Guy Kuo)\nSubject: SI Clock Poll - Final Call\nSummary: Final call for SI clock reports\nKeywords: SI,acceleration,clock,upgrade\nArticle-I.D.: shelley.1qvfo9INNc3s\nOrganization: University of Washington\nLines: 11\nNNTP-Posting-Host: carson.u.washington.edu\n\nA fair number of brave souls who upgraded their SI clock oscillator have\nshared their experiences for this poll. Please send a brief message detailing\nyour experiences with the procedure. Top speed attained, CPU rated speed,\nadd on cards and adapters, heat sinks, hour of usage per day, floppy disk\nfunctionality with 800 and 1.4 m floppies are especially requested.\n\nI will be summarizing in the next two days, so please add to the network\nknowledge base if you have done the clock upgrade and haven't answered this\npoll. Thanks.\n\nGuy Kuo <guykuo@u.washington.edu>\n"

In [13]:
# Convertir a una lista
data = df.content.values.tolist()
pprint(data[:1])

["From: lerxst@wam.umd.edu (where's my thing)\n"
 'Subject: WHAT car is this!?\n'
 'Nntp-Posting-Host: rac3.wam.umd.edu\n'
 'Organization: University of Maryland, College Park\n'
 'Lines: 15\n'
 '\n'
 ' I was wondering if anyone out there could enlighten me on this car I saw\n'
 'the other day. It was a 2-door sports car, looked to be from the late 60s/\n'
 'early 70s. It was called a Bricklin. The doors were really small. In '
 'addition,\n'
 'the front bumper was separate from the rest of the body. This is \n'
 'all I know. If anyone can tellme a model name, engine specs, years\n'
 'of production, where this car is made, history, or whatever info you\n'
 'have on this funky looking car, please e-mail.\n'
 '\n'
 'Thanks,\n'
 '- IL\n'
 '   ---- brought to you by your neighborhood Lerxst ----\n'
 '\n'
 '\n'
 '\n'
 '\n']


In [14]:
# Eliminar emails
data = [re.sub(r'\S*@\S*\s?', '', sent) for sent in data]
pprint(data[:1])

["From: (where's my thing)\n"
 'Subject: WHAT car is this!?\n'
 'Nntp-Posting-Host: rac3.wam.umd.edu\n'
 'Organization: University of Maryland, College Park\n'
 'Lines: 15\n'
 '\n'
 ' I was wondering if anyone out there could enlighten me on this car I saw\n'
 'the other day. It was a 2-door sports car, looked to be from the late 60s/\n'
 'early 70s. It was called a Bricklin. The doors were really small. In '
 'addition,\n'
 'the front bumper was separate from the rest of the body. This is \n'
 'all I know. If anyone can tellme a model name, engine specs, years\n'
 'of production, where this car is made, history, or whatever info you\n'
 'have on this funky looking car, please e-mail.\n'
 '\n'
 'Thanks,\n'
 '- IL\n'
 '   ---- brought to you by your neighborhood Lerxst ----\n'
 '\n'
 '\n'
 '\n'
 '\n']


In [16]:
# Eliminar newlines
data = [re.sub(r'\s+', ' ', sent) for sent in data]
pprint(data[:1])

["From: (where's my thing) Subject: WHAT car is this!? Nntp-Posting-Host: "
 'rac3.wam.umd.edu Organization: University of Maryland, College Park Lines: '
 '15 I was wondering if anyone out there could enlighten me on this car I saw '
 'the other day. It was a 2-door sports car, looked to be from the late 60s/ '
 'early 70s. It was called a Bricklin. The doors were really small. In '
 'addition, the front bumper was separate from the rest of the body. This is '
 'all I know. If anyone can tellme a model name, engine specs, years of '
 'production, where this car is made, history, or whatever info you have on '
 'this funky looking car, please e-mail. Thanks, - IL ---- brought to you by '
 'your neighborhood Lerxst ---- ']


In [17]:
# Eliminar comillas
data = [re.sub(r"\'", "", sent) for sent in data]
pprint(data[:1])

['From: (wheres my thing) Subject: WHAT car is this!? Nntp-Posting-Host: '
 'rac3.wam.umd.edu Organization: University of Maryland, College Park Lines: '
 '15 I was wondering if anyone out there could enlighten me on this car I saw '
 'the other day. It was a 2-door sports car, looked to be from the late 60s/ '
 'early 70s. It was called a Bricklin. The doors were really small. In '
 'addition, the front bumper was separate from the rest of the body. This is '
 'all I know. If anyone can tellme a model name, engine specs, years of '
 'production, where this car is made, history, or whatever info you have on '
 'this funky looking car, please e-mail. Thanks, - IL ---- brought to you by '
 'your neighborhood Lerxst ---- ']


In [18]:
def sentences_to_words(sentences):
    words = []
    for sentence in sentences:
        # https://radimrehurek.com/gensim/utils.html#gensim.utils.simple_preprocess
        words.append(gensim.utils.simple_preprocess(str(sentence), deacc=True))
        
    return words

data_words = sentences_to_words(data)

print(data_words[:1])

[['from', 'wheres', 'my', 'thing', 'subject', 'what', 'car', 'is', 'this', 'nntp', 'posting', 'host', 'rac', 'wam', 'umd', 'edu', 'organization', 'university', 'of', 'maryland', 'college', 'park', 'lines', 'was', 'wondering', 'if', 'anyone', 'out', 'there', 'could', 'enlighten', 'me', 'on', 'this', 'car', 'saw', 'the', 'other', 'day', 'it', 'was', 'door', 'sports', 'car', 'looked', 'to', 'be', 'from', 'the', 'late', 'early', 'it', 'was', 'called', 'bricklin', 'the', 'doors', 'were', 'really', 'small', 'in', 'addition', 'the', 'front', 'bumper', 'was', 'separate', 'from', 'the', 'rest', 'of', 'the', 'body', 'this', 'is', 'all', 'know', 'if', 'anyone', 'can', 'tellme', 'model', 'name', 'engine', 'specs', 'years', 'of', 'production', 'where', 'this', 'car', 'is', 'made', 'history', 'or', 'whatever', 'info', 'you', 'have', 'on', 'this', 'funky', 'looking', 'car', 'please', 'mail', 'thanks', 'il', 'brought', 'to', 'you', 'by', 'your', 'neighborhood', 'lerxst']]


In [19]:
# Construimos modelos de bigrams y trigrams
# https://radimrehurek.com/gensim/models/phrases.html#gensim.models.phrases.Phrases
bigram = gensim.models.Phrases(data_words, min_count=5, threshold=10)
trigram = gensim.models.Phrases(bigram[data_words], threshold=10)

# Aplicamos el conjunto de bigrams/trigrams a nuestros documentos
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

In [16]:
print(data_words[0])
print(bigram_mod[data_words[0]])
print(trigram_mod[bigram_mod[data_words[0]]])

['from', 'wheres', 'my', 'thing', 'subject', 'what', 'car', 'is', 'this', 'nntp', 'posting', 'host', 'rac', 'wam', 'umd', 'edu', 'organization', 'university', 'of', 'maryland', 'college', 'park', 'lines', 'was', 'wondering', 'if', 'anyone', 'out', 'there', 'could', 'enlighten', 'me', 'on', 'this', 'car', 'saw', 'the', 'other', 'day', 'it', 'was', 'door', 'sports', 'car', 'looked', 'to', 'be', 'from', 'the', 'late', 'early', 'it', 'was', 'called', 'bricklin', 'the', 'doors', 'were', 'really', 'small', 'in', 'addition', 'the', 'front', 'bumper', 'was', 'separate', 'from', 'the', 'rest', 'of', 'the', 'body', 'this', 'is', 'all', 'know', 'if', 'anyone', 'can', 'tellme', 'model', 'name', 'engine', 'specs', 'years', 'of', 'production', 'where', 'this', 'car', 'is', 'made', 'history', 'or', 'whatever', 'info', 'you', 'have', 'on', 'this', 'funky', 'looking', 'car', 'please', 'mail', 'thanks', 'il', 'brought', 'to', 'you', 'by', 'your', 'neighborhood', 'lerxst']
['from', 'wheres', 'my', 'thing

In [20]:
# python3 -m spacy download en_core_web_trf
# Inicializamos el modelo 'en_core_web_lg' con las componentes de POS únicamente
nlp = spacy.load('en_core_web_trf', disable=['parser', 'ner'])

In [21]:
# Eliminar stopwords
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

# Hacer bigrams
def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]

# Hacer trigrams
def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

# Lematización basada en el modelo de POS de Spacy
"""
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    texts_out = []
    for sent in texts:
        print(sent)
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out
"""
def lemmatization(texts):
    return texts

In [22]:
# Eliminamos stopwords
data_words_nostops = remove_stopwords(data_words)

In [54]:
data_words_nostops[0]

['wheres',
 'thing',
 'car',
 'nntp',
 'posting',
 'host',
 'rac',
 'wam',
 'umd',
 'organization',
 'university',
 'maryland',
 'college',
 'park',
 'lines',
 'wondering',
 'anyone',
 'could',
 'enlighten',
 'car',
 'saw',
 'day',
 'door',
 'sports',
 'car',
 'looked',
 'late',
 'early',
 'called',
 'bricklin',
 'doors',
 'really',
 'small',
 'addition',
 'front',
 'bumper',
 'separate',
 'rest',
 'body',
 'know',
 'anyone',
 'tellme',
 'model',
 'name',
 'engine',
 'specs',
 'years',
 'production',
 'car',
 'made',
 'history',
 'whatever',
 'info',
 'funky',
 'looking',
 'car',
 'please',
 'mail',
 'thanks',
 'il',
 'brought',
 'neighborhood',
 'lerxst']

In [23]:
# Formamos bigrams
data_words_bigrams = make_bigrams(data_words_nostops)

In [56]:
data_words_bigrams[:1]

[['wheres',
  'thing',
  'car',
  'nntp_posting',
  'host_rac',
  'wam_umd',
  'organization_university',
  'maryland_college',
  'park',
  'lines',
  'wondering',
  'anyone',
  'could',
  'enlighten',
  'car',
  'saw',
  'day',
  'door',
  'sports_car',
  'looked',
  'late_early',
  'called',
  'bricklin',
  'doors',
  'really',
  'small',
  'addition',
  'front_bumper',
  'separate',
  'rest',
  'body',
  'know',
  'anyone',
  'tellme',
  'model',
  'name',
  'engine',
  'specs',
  'years',
  'production',
  'car',
  'made',
  'history',
  'whatever',
  'info',
  'funky',
  'looking',
  'car',
  'please_mail',
  'thanks',
  'il',
  'brought',
  'neighborhood',
  'lerxst']]

In [24]:
data_words_trigrams = make_trigrams(data_words_bigrams)

In [58]:
data_words_trigrams

[['wheres',
  'thing',
  'car',
  'nntp_posting_host_rac',
  'wam_umd',
  'organization_university',
  'maryland_college_park',
  'lines',
  'wondering',
  'anyone',
  'could',
  'enlighten',
  'car',
  'saw',
  'day',
  'door',
  'sports_car',
  'looked',
  'late_early',
  'called',
  'bricklin',
  'doors',
  'really',
  'small',
  'addition',
  'front_bumper',
  'separate',
  'rest',
  'body',
  'know',
  'anyone',
  'tellme',
  'model',
  'name',
  'engine',
  'specs',
  'years',
  'production',
  'car',
  'made',
  'history',
  'whatever',
  'info',
  'funky',
  'looking',
  'car',
  'please_mail',
  'thanks',
  'il',
  'brought',
  'neighborhood',
  'lerxst'],
 ['guy_kuo',
  'si_clock',
  'poll',
  'final',
  'call',
  'summary',
  'final',
  'call',
  'si_clock',
  'reports',
  'keywords',
  'si',
  'acceleration',
  'clock',
  'upgrade',
  'article_shelley',
  'qvfo',
  'innc',
  'organization_university',
  'washington_lines_nntp',
  'posting_host_carson_washington',
  'fair',


In [25]:
# Lematizamos preservando únicamente noun, adj, vb, adv
data_lemmatized = lemmatization(data_words_trigrams)

print(data_lemmatized[:1])

[['wheres', 'thing', 'car', 'nntp_posting_host_rac', 'wam_umd', 'organization_university', 'maryland_college_park', 'lines', 'wondering', 'anyone', 'could', 'enlighten', 'car', 'saw', 'day', 'door', 'sports_car', 'looked', 'late_early', 'called', 'bricklin', 'doors', 'really', 'small', 'addition', 'front_bumper', 'separate', 'rest', 'body', 'know', 'anyone', 'tellme', 'model', 'name', 'engine', 'specs', 'years', 'production', 'car', 'made', 'history', 'whatever', 'info', 'funky', 'looking', 'car', 'please_mail', 'thanks', 'il', 'brought', 'neighborhood', 'lerxst']]


In [26]:
# Creamos diccionario
id2word = corpora.Dictionary(data_lemmatized)

In [24]:
for key, value in id2word.items():
    print(key, value)

0 addition
1 anyone
2 body
3 bricklin
4 brought
5 called
6 car
7 could
8 day
9 door
10 doors
11 engine
12 enlighten
13 front_bumper
14 funky
15 history
16 il
17 info
18 know
19 late_early
20 lerxst
21 lines
22 looked
23 looking
24 made
25 maryland_college_park
26 model
27 name
28 neighborhood
29 nntp_posting_host_rac
30 organization_university
31 please_mail
32 production
33 really
34 rest
35 saw
36 separate
37 small
38 specs
39 sports_car
40 tellme
41 thanks
42 thing
43 wam_umd
44 whatever
45 wheres
46 wondering
47 years
48 acceleration
49 adapters
50 add
51 answered
52 article_shelley
53 attained
54 base
55 brave
56 brief
57 call
58 cards
59 clock
60 cpu
61 detailing
62 done
63 especially
64 experiences
65 fair
66 final
67 floppies
68 floppy_disk
69 functionality
70 guy_kuo
71 havent
72 heat_sinks
73 hour
74 innc
75 keywords
76 knowledge
77 message
78 network
79 next
80 number
81 oscillator
82 per_day
83 please
84 please_send
85 poll
86 posting_host_carson_washington
87 procedure
88 

39700 carcinogens
39701 catalyzes
39702 charcoal
39703 cooking
39704 drips
39705 health_risk
39706 lava
39707 liquifies
39708 richard_silver
39709 spot_colorado
39710 carrying_case
39711 cheever
39712 cleaned
39713 phono
39714 preamplifier
39715 selectors
39716 subharmonic
39717 tuner
39718 brandeis
39719 congregations
39720 deceive
39721 divinely_inspired
39722 english_translations
39723 gracious
39724 iterations
39725 kjv
39726 multiplicity
39727 nasb
39728 prominantly
39729 translating
39730 amenable
39731 autobahns
39732 autostrade
39733 barges
39734 buffeting
39735 cannon
39736 cruise_control
39737 daffy
39738 dediu
39739 detriment
39740 distinguished
39741 ganguly
39742 gasoline
39743 got_caught
39744 gras
39745 guardrail
39746 horace
39747 inc_austin
39748 knuckles
39749 mardi
39750 marquee
39751 marquees
39752 mercs
39753 misperception
39754 motorola_inc
39755 poise
39756 pothole
39757 ratios
39758 revved
39759 sdl
39760 shantanu
39761 smelliest
39762 stall
39763 sucker
39764 t

78636 vangelis
78637 vasilis
78638 voglis
78639 azzim
78640 celebrations
78641 checkpoint
78642 danced
78643 ealyan
78644 free_sample
78645 golani
78646 hajras
78647 hamdan
78648 holiest
78649 israeli_troops
78650 jamea
78651 khansaa
78652 makhloufs
78653 parakeets
78654 practising
78655 qdieh
78656 schoolgirls
78657 sepulchre
78658 spate
78659 srur
78660 tell_em_arf
78661 washinton
78662 worshippers
78663 younis
78664 zamno
78665 esn
78666 lavergne
78667 wnt
78668 childern
78669 goons
78670 vlx
78671 admans
78672 dales
78673 deleta
78674 forking
78675 kludging
78676 overcharge
78677 overcharges
78678 tending
78679 toasty
78680 underspecified
78681 confucius
78682 divya
78683 eecae
78684 kolodzie
78685 psychologisches
78686 angolan
78687 dhimini
78688 taacman
78689 zijdenbos
78690 bridgman
78691 lacelle
78692 ottwawa
78693 sexton
78694 gutmann
78695 thwim
78696 ansa
78697 leistritz
78698 remus
78699 welker
78700 ntua
78701 czeriew
78702 czerkawski
78703 eliteserien
78704 hammarby
78705

In [27]:
# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 1), (1, 2), (2, 1), (3, 1), (4, 1), (5, 1), (6, 4), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1)]]


In [26]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]

[[('addition', 1),
  ('anyone', 2),
  ('body', 1),
  ('bricklin', 1),
  ('brought', 1),
  ('called', 1),
  ('car', 4),
  ('could', 1),
  ('day', 1),
  ('door', 1),
  ('doors', 1),
  ('engine', 1),
  ('enlighten', 1),
  ('front_bumper', 1),
  ('funky', 1),
  ('history', 1),
  ('il', 1),
  ('info', 1),
  ('know', 1),
  ('late_early', 1),
  ('lerxst', 1),
  ('lines', 1),
  ('looked', 1),
  ('looking', 1),
  ('made', 1),
  ('maryland_college_park', 1),
  ('model', 1),
  ('name', 1),
  ('neighborhood', 1),
  ('nntp_posting_host_rac', 1),
  ('organization_university', 1),
  ('please_mail', 1),
  ('production', 1),
  ('really', 1),
  ('rest', 1),
  ('saw', 1),
  ('separate', 1),
  ('small', 1),
  ('specs', 1),
  ('sports_car', 1),
  ('tellme', 1),
  ('thanks', 1),
  ('thing', 1),
  ('wam_umd', 1),
  ('whatever', 1),
  ('wheres', 1),
  ('wondering', 1),
  ('years', 1)]]

## Latent Dirichlet Allocation

![Latent Dirichlet Allocation](https://miro.medium.com/max/1400/1*fCc0JT3W-1ViYyw0hJ7rdA.jpeg)

In [28]:
lda_model = gensim.models.ldamodel.LdaModel(
    corpus=corpus,
    id2word=id2word,
    num_topics=10, 
    random_state=100,
    update_every=1,
    chunksize=100,
    passes=10,
    alpha='auto',
    # beta=1,
    per_word_topics=True
)

In [90]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())

[(0,
  '0.021*"space" + 0.013*"disk" + 0.011*"moon" + 0.010*"nasa" + 0.010*"pens" + '
  '0.010*"cheaper" + 0.009*"earth" + 0.008*"orbit" + 0.008*"mission" + '
  '0.008*"launch"'),
 (1,
  '0.061*"ax_ax_ax_ax" + 0.013*"c_" + 0.010*"dn" + 0.009*"cx" + 0.008*"um" + '
  '0.007*"ei" + 0.006*"em" + 0.006*"gm" + 0.006*"max_ax_ax_ax" + '
  '0.006*"ax_max_ax_ax"'),
 (2,
  '0.014*"program" + 0.013*"software" + 0.012*"windows" + 0.010*"file" + '
  '0.009*"mac" + 0.008*"hardware" + 0.008*"available" + 0.008*"version" + '
  '0.008*"ripem" + 0.007*"files"'),
 (3,
  '0.019*"drive" + 0.011*"season" + 0.010*"mb" + 0.008*"telnet" + '
  '0.008*"jumper" + 0.008*"scsi" + 0.008*"os" + 0.007*"busmastering" + '
  '0.007*"mouse" + 0.007*"chicago"'),
 (4,
  '0.015*"family" + 0.011*"shows" + 0.009*"constitution" + 0.009*"eat" + '
  '0.009*"ride" + 0.008*"article_mark" + 0.008*"intel" + 0.008*"motorcycle" + '
  '0.007*"sigh" + 0.006*"contain"'),
 (5,
  '0.007*"year" + 0.007*"team" + 0.007*"game" + 0.006*"new" + 0.

In [91]:
lda_model.alpha

array([0.17470227, 0.22825523, 0.5838317 , 0.3331926 , 0.20275997,
       1.3656858 , 1.5471847 , 3.7867637 , 1.7223003 , 0.50705504],
      dtype=float32)

In [29]:
doc_lda = lda_model[corpus]
print(doc_lda)

In [30]:
# Score de coherencia
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Coherence Score:  0.52224748346135


In [31]:
test_texts = ["The Moon orbits the Earth sports car"]

In [32]:
test_words = sentences_to_words(test_texts)
print(test_words)

[['the', 'moon', 'orbits', 'the', 'earth', 'sports', 'car']]


In [33]:
tests_words_nostops = remove_stopwords(test_words)
print(tests_words_nostops)

[['moon', 'orbits', 'earth', 'sports', 'car']]


In [34]:
tests_words_bigrams = make_bigrams(tests_words_nostops)
print(tests_words_bigrams)

[['moon', 'orbits', 'earth', 'sports_car']]


In [35]:
tests_words_trigrams = make_trigrams(tests_words_bigrams)
print(tests_words_trigrams)

[['moon', 'orbits', 'earth', 'sports_car']]


In [36]:
tests_words_bow = [id2word.doc2bow(text) for text in tests_words_trigrams]
print(tests_words_bow)

[[(39, 1), (2092, 1), (3837, 1), (19013, 1)]]


In [37]:
lda_model.get_document_topics(tests_words_bow[0])

[(0, 0.2135743),
 (1, 0.01579953),
 (2, 0.10933102),
 (3, 0.023063153),
 (4, 0.014034779),
 (5, 0.094531015),
 (6, 0.10709412),
 (7, 0.26211476),
 (8, 0.12535961),
 (9, 0.03509769)]